In [1]:
%cd ..

/Users/Yaroslav.Sokolov/PycharmProjects/optimization_methods


In [2]:
from logistic_regression.experiment import Experiment
from logistic_regression.oracle import Oracle
import numpy as np

In [3]:
oracles = {
    "a1a": Oracle.make_oracle("logistic_regression/data/a1a.txt", "libsvm"),
    "breast": Oracle.make_oracle("logistic_regression/data/breast-cancer_scale.txt", "libsvm"),
    "random": Oracle.make_oracle("logistic_regression/data/generated.tsv", "tsv"),
}

## Пример использования Lasso оптимизатора с проксимальным оператором

In [4]:
w_opt, stat = Experiment.make_experiment(
                oracles["a1a"],
                optimizer="lasso",
                start_point=np.zeros(oracles["a1a"].dim),
                tol=1e-8,
                max_iter=10000,
                regularization_coeff=1e-2,
)

## Пункты 1. 2. и 3.
Давайте построим сразу все графики и посмотрим на них:

In [5]:
Experiment.draw_lasso_figs(
    oracles["a1a"],
    start_point=np.zeros(oracles["a1a"].dim),
    tol=1e-8,
    max_iter=10000,
    regularization_coeffs=np.logspace(-4.5, -1, 10),
)

100%|██████████| 10/10 [00:09<00:00,  1.00it/s]


## 1. Скорость работы
Как мы видим, скорость работы уменьшается при увеличении коэффицента регуляризации. Связано это напрямую с тем фактом, что количество итераций уменьшается при увеличении коэффицента регуляризации.

Также мы чуть позже увидим, что _Lasso_ работает так же быстро, как и _GD_.

## 2.1 Скорость сходимости
Скорость сходимости увеличивается при увеличении коэффицента регуляризации. 

Я точно не знаю, с чем это связано, но догадываюсь, что это происходит из-за того, оптимальная точка становится ближе к стартовой (нули). С инженерной же точки зрения, норма, по которой происходит остановка, уменьшается при уменьшении числа ненулевых компонентов вектора `w`. Поэтому алгоритм останавливется раньше, когда нулевых компонент в `w` больше.

Если же мы стартуем не из нуля, то алгоритм загонет бесполезные компоненты `w` в $0$ за число итераций, зависящих только от $\lambda$ и стартовой величины компонент.

Стоит заметить, что значение функции потерь выходит на плато для всех $\lambda$ примерно за одинаковое количество операций, так что вопрос здесь только в том, как быстро алгоритм сумеет выйти по критерию остановки.

## 2.1 Количество ненулевых компонент
Количество ненулевых компонент уменьшается с ростом $\lambda$, как и должно, ведь $\lambda$ -- это сила регуляризации.

## 3.1 Графики функции потерь
Функция потерь тем больше, чем больше $\lambda$, что совершенно логично, ведь мы смотриф на функцию потерь на тренировочных данных. То есть мы отдаляем точку минимума от настоящего оптимума, поэтому величина функции только растёт с ростом $\lambda$.

## 3.2 Графики критерия остановки
Здесь наглядно видно то, что было описано в пункте `2.1`. А именно, при увеличении $\lambda$ величина из критерии остановки уменьшается гораздо быстрее.

## Сравнение с GD

In [6]:
_, stat_gd = Experiment.make_experiment(
                oracles["a1a"],
                optimizer="GD",
                line_search="nesterov",
                start_point=np.zeros(oracles["a1a"].dim),
                tol=1e-8,
                max_iter=1000,
)

_, stat_lasso_zero = Experiment.make_experiment(
                oracles["a1a"],
                optimizer="lasso",
                start_point=np.zeros(oracles["a1a"].dim),
                tol=1e-8,
                max_iter=1000,
                regularization_coeff=0.0,
)

_, stat_lasso = Experiment.make_experiment(
                oracles["a1a"],
                optimizer="lasso",
                start_point=np.zeros(oracles["a1a"].dim),
                tol=1e-8,
                max_iter=1000,
                regularization_coeff=1e-3,
)

In [7]:
Experiment.draw_figs(["GD", r"$\lambda = 0$", r"$\lambda = 1e-3$"],
                     stats=[stat_gd, stat_lasso_zero, stat_lasso],
                     axes=("iters", "times"),
                     dataset_name="a1a")

### GD и Lasso при lambda=0
Значения функции потерь этих двух алгоритмов довольно близки, что говорит о том, что _Lasso_ c $\lambda=0$ действительно похож на _GD_.

Время работы тоже сопоставимо. То есть полученный алгоритм с использованием проксимального оператора работает за то же время, что и _GD_.

#### Далее сравним скорость сходимости из плохой стартовой точки.

In [8]:
_, stat_gd = Experiment.make_experiment(
                oracles["a1a"],
                optimizer="GD",
                line_search="nesterov",
                start_point=np.zeros(oracles["a1a"].dim) + 4,
                tol=1e-8,
                max_iter=1000,
)

_, stat_lasso = Experiment.make_experiment(
                oracles["a1a"],
                optimizer="lasso",
                start_point=np.zeros(oracles["a1a"].dim) + 4,
                tol=1e-8,
                max_iter=1000,
                regularization_coeff=1e-1,
)

Experiment.draw_figs(["GD", r"$\lambda = 1e-1$"],
                     stats=[stat_gd, stat_lasso],
                     axes=("iters", "times"),
                     dataset_name="a1a")

При достаточно большом $\lambda$ _Lasso_ начинает сходиться при старте из плохой точки, в отличие от _GD_. Что логично, ведь у нас функция становится лучше на экстремальных значениях.

## Исследование на других датасетах
Далее я просто построю те же графики для других датаестов и прокомментрию интересные вещи, если они будут.

### Breast cancer

In [9]:
Experiment.draw_lasso_figs(
    oracles["breast"],
    start_point=np.zeros(oracles["breast"].dim),
    tol=1e-8,
    max_iter=10000,
    regularization_coeffs=np.logspace(-4.5, -1, 10),
)

100%|██████████| 10/10 [00:00<00:00, 18.41it/s]


## Скорость работы
Довольно странный выброс в районе $\lambda=1e-4$. Видимо это связано с довольно странным графиком критерия остановки. Почему-то при средних значениях $\lambda$ появляется странное плато.

Со всем остальным картина примерно такая же.